# **Plan Of Attack:**

1) ***IMPORT MODEL*** : we are going to use ResNET CNN model for this project. ResNET model is already trained model, made by many computer scientists and data scientists which is trained on various Images from IMAGENET with very great accuracy and hence we use it. We could have used our own CNN but that would have not gived us the accuracy as high as ResNET.

2) ***EXTRACT FEATURES:*** We are going to have image of (224,224,3) resolution image for which we have to find matches for suggesting similar products. ResNET has trained on 44k images and hence we need to compare the uploaded image with all those 44k images pixels by pixels in order to find the similar products. since this becomes near to impossible task, hence we go for comparing primitive or complex features of all the 44k images with the features obtained for the uploaded image (features will be extracted by our ResNET CNN model for both 44k images and uploaded one). Comparing features makes the task easy as we are in total going to have 2048 features for each of the images. Therefore what we will have is a matrix of size (44k x 2048) where rows are all the 44k images on which ResNET is trained and (1 x 2048) vector for uploaded image.

3) ***GENERATE RECOMMONDATIONS:*** In order to generate recommondations we are going to calculate euclidian distance (knn will be used from sklearn to calculate the distance) for all the rows of the feature matrix with the feature vector we got for uploaded image. Whichever rows have closest distance with the feature vector, they will be considered as our recommondations and will be shown to user.

In [1]:
import tensorflow as tf
tf.config.list_physical_devices('GPU')

[PhysicalDevice(name='/physical_device:GPU:0', device_type='GPU')]

In [2]:
gpus = tf.config.experimental.list_physical_devices('GPU')
for gpu in gpus:
    tf.config.experimental.set_memory_growth(gpu, True)

In [3]:
'''lets import model'''
import pickle
from tqdm import tqdm
import os
import numpy as np
from numpy.linalg import norm
import tensorflow
from tensorflow.keras.preprocessing import image
from tensorflow.keras.layers import GlobalMaxPooling2D
from tensorflow.keras.applications.resnet50 import ResNet50,preprocess_input

In [4]:
model = ResNet50(weights='imagenet', include_top=False, input_shape=(224,224,3))
'''so basically we have asked for the weights value which ResNet50 have calculated on imagenet dataset and we have kept
include_top=False that means we are not wanting the o/p layer (o/p lyr of conv. layer) and we will create our own one.
also our dataset i/p size is given here.'''

model.trainable = False

'''resnet is already trained model and hence we need to keep it false'''

#now we add our own top layer:
model = tensorflow.keras.Sequential([
    model,
    GlobalMaxPooling2D()
])

'''so what we did is we used ResNet50 model with last layer of GlobalMaxPooling and you know why we used that at last
(flatten k jgah use kiye)'''

model.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 resnet50 (Functional)       (None, 7, 7, 2048)        23587712  
                                                                 
 global_max_pooling2d (Globa  (None, 2048)             0         
 lMaxPooling2D)                                                  
                                                                 
Total params: 23,587,712
Trainable params: 0
Non-trainable params: 23,587,712
_________________________________________________________________


In [5]:
# Now we form a function which will extract features from the 44k images and also the uploaded image using resnet.
def extract_features(img_path,model):
  img = image.load_img(img_path, target_size=(224,224))
  img_array = image.img_to_array(img) # converting image to a numpy array of size (224,224,3) since its a rgb image.
  expanded_img_array = np.expand_dims(img_array, axis = 0) # expanded 3d image to 4d as it is suitable for resnet (1,224,224,3)
  preprocessing_img = preprocess_input(expanded_img_array) #same thing we are preprocessing the img according to the needs of ResNet
  result = model.predict(preprocessing_img).flatten() # this is how we get the feature map for the image.
  '''please keep in mind that the prediction is made only for convolutional layers and since we are not doing any
  classification here hence we din't used fully connected layer for classification. Hence we get a feature map of size:
    (1,2048) after global_max_pooling o/p layer. At last we use flatten to make it 2048 from (1,2048) since we expanded_img_array.'''
  normalized_result = result/norm(result)  # normalize kiya hai sirf and you know why we do normalization.
  return normalized_result

In [6]:
# Now what we do is we get a complete path for each of the image file of the 44k image.
filenames = []
for file in os.listdir('images'):
    filenames.append(os.path.join('images',file)) 
print(len(filenames))
print(filenames[0:5])

44441
['images\\10000.jpg', 'images\\10001.jpg', 'images\\10002.jpg', 'images\\10003.jpg', 'images\\10004.jpg']


In [7]:
# Define batch size
batch_size = 32

# Initialize feature and filename lists
feature_list = []
filenames = []

# Get the filenames and their complete paths
for file in os.listdir('images'):
    filenames.append(os.path.join('images', file))

# Process images in batches
for batch_start in tqdm(range(0, len(filenames), batch_size)):
    batch_end = min(batch_start + batch_size, len(filenames))
    batch_files = filenames[batch_start:batch_end]

    # Extract features for each image in the batch
    batch_features = [extract_features(file, model) for file in batch_files]
    feature_list.append(batch_features)

# Save the features
pickle.dump(feature_list, open('features.pkl', 'wb'))

# Print the shape of the feature list
print(np.array(feature_list).shape)


  0%|                                                                                         | 0/1389 [00:00<?, ?it/s]

1/1 [==============================] - 0s 26ms/step


  0%|                                                                               | 1/1389 [00:09<3:37:53,  9.42s/it]

1/1 [==============================] - 0s 26ms/step


  0%|                                                                               | 2/1389 [00:12<2:11:05,  5.67s/it]

...

1/1 [==============================] - 0s 79ms/step


100%|███████████████████████████████████████████████████████████████████████████▉| 1388/1389 [1:55:11<00:07,  7.54s/it]

1/1 [==============================] - 0s 79ms/step


100%|████████████████████████████████████████████████████████████████████████████| 1389/1389 [1:55:17<00:00,  4.98s/it]


ValueError: setting an array element with a sequence. The requested array has an inhomogeneous shape after 1 dimensions. The detected shape was (1389,) + inhomogeneous part.

In [19]:
np.array(feature_list[0]).shape

(32, 2048)

In [20]:
feature_list

[[array([0.        , 0.01765356, 0.0017578 , ..., 0.01228944, 0.02714405,
         0.06902912], dtype=float32),
  array([0.        , 0.0365388 , 0.        , ..., 0.00996548, 0.02371446,
         0.04649271], dtype=float32),
  array([0.        , 0.03639553, 0.00711491, ..., 0.00148193, 0.        ,
         0.0543252 ], dtype=float32),
  array([0.00224676, 0.05031323, 0.00747729, ..., 0.00347652, 0.03385967,
         0.04565524], dtype=float32),
  array([0.0031157 , 0.0623952 , 0.        , ..., 0.00168183, 0.02022591,
         0.05840961], dtype=float32),
  array([0.        , 0.10474795, 0.00199814, ..., 0.        , 0.03015194,
         0.02719432], dtype=float32),
  array([0.        , 0.12431607, 0.01466206, ..., 0.00290041, 0.04062055,
         0.0653232 ], dtype=float32),
  array([0.        , 0.09182027, 0.01563613, ..., 0.        , 0.00505128,
         0.04561693], dtype=float32),
  array([0.        , 0.0954417 , 0.01152262, ..., 0.0007493 , 0.04519923,
         0.07663859], dtype=fl

In [ ]:
# Rearranging the feature_list shape:
new_feature_list = np.zeros((44441,2048))
j=0
for items in range(0,1388):
    new_feature_list[j:j+32,:] = np.array(feature_list[items])
    j=j+32

In [ ]:
pickle.dump(new_feature_list,open('features.pkl','wb'))

In [ ]:
pickle.dump(filenames,open('filenames.pkl','wb'))